# Motor creation and export

This example uses PyAEDT to create a RMxprt project and export it to Maxwell 2D.
It shows how to create an ASSM (Adjust-Speed Synchronous Machine) in RMxprt
and how to access rotor and stator settings.
It then exports the model to a Maxwell 2D design
and the RMxprt settings to a JSON file to be reused.

Keywords: **RMxprt**, **Maxwell 2D**

## Perform imports and define constants

Perform required imports.

In [1]:
import os
import tempfile
import time

In [2]:
import ansys.aedt.core

Define constants.

In [3]:
AEDT_VERSION = "2024.2"
NUM_CORES = 4
NG_MODE = False  # Open AEDT UI when it is launched.

## Create temporary directory

Create a temporary directory where downloaded data or
dumped data can be stored.
If you'd like to retrieve the project data for subsequent use,
the temporary folder name is given by ``temp_folder.name``.

In [4]:
temp_folder = tempfile.TemporaryDirectory(suffix=".ansys")

## Launch AEDT and RMxprt

Launch AEDT and RMxprt after first setting up the project name.
This example uses ASSM (Adjust-Speed Synchronous Machine) as the solution type.

In [5]:
project_name = os.path.join(temp_folder.name, "ASSM.aedt")
rmxprt = ansys.aedt.core.Rmxprt(
    version=AEDT_VERSION,
    new_desktop=True,
    close_on_exit=True,
    solution_type="ASSM",
    project=project_name,
    non_graphical=NG_MODE,
)

PyAEDT INFO: Python version 3.10.11 (tags/v3.10.11:7d4cc5a, Apr  5 2023, 00:38:17) [MSC v.1929 64 bit (AMD64)]


PyAEDT INFO: PyAEDT version 0.12.dev0.


PyAEDT INFO: Initializing new Desktop session.


PyAEDT INFO: Log on console is enabled.


PyAEDT INFO: Log on file C:\Users\ansys\AppData\Local\Temp\pyaedt_ansys_93b32be7-acde-4ddd-9bb3-5ffc80a22478.log is enabled.


...

PyAEDT INFO: Project ASSM has been created.


PyAEDT INFO: No design is present. Inserting a new design.


PyAEDT INFO: Added design 'RMxprtSolution_HTO' of type RMxprtSolution.


PyAEDT INFO: Aedt Objects correctly read


PyAEDT INFO: ModelerRMxprt class has been initialized! Elapsed time: 0m 0sec


## Define global machine settings

In [6]:
rmxprt.general["Number of Poles"] = 4
rmxprt.general["Rotor Position"] = "Inner Rotor"
rmxprt.general["Frictional Loss"] = "12W"
rmxprt.general["Windage Loss"] = "0W"
rmxprt.general["Reference Speed"] = "1500rpm"
rmxprt.general["Control Type"] = "DC"
rmxprt.general["Circuit Type"] = "Y3"

## Define circuit settings

In [7]:
rmxprt.circuit["Trigger Pulse Width"] = "120deg"
rmxprt.circuit["Transistor Drop"] = "2V"
rmxprt.circuit["Diode Drop"] = "2V"

## Define stator

Define stator and slot and winding settings.

In [8]:
rmxprt.stator["Outer Diameter"] = "122mm"
rmxprt.stator["Inner Diameter"] = "75mm"
rmxprt.stator["Length"] = "65mm"
rmxprt.stator["Stacking Factor"] = 0.95
rmxprt.stator["Steel Type"] = "steel_1008"
rmxprt.stator["Number of Slots"] = 24
rmxprt.stator["Slot Type"] = 2

In [9]:
rmxprt.stator.properties.children["Slot"].props["Auto Design"] = False
rmxprt.stator.properties.children["Slot"].props["Hs0"] = "0.5mm"
rmxprt.stator.properties.children["Slot"].props["Hs1"] = "1.2mm"
rmxprt.stator.properties.children["Slot"].props["Hs2"] = "8.2mm"
rmxprt.stator.properties.children["Slot"].props["Bs0"] = "2.5mm"
rmxprt.stator.properties.children["Slot"].props["Bs1"] = "5.6mm"
rmxprt.stator.properties.children["Slot"].props["Bs2"] = "7.6mm"

In [10]:
rmxprt.stator.properties.children["Winding"].props["Winding Layers"] = 2
rmxprt.stator.properties.children["Winding"].props["Parallel Branches"] = 1
rmxprt.stator.properties.children["Winding"].props["Conductors per Slot"] = 52
rmxprt.stator.properties.children["Winding"].props["Coil Pitch"] = 5
rmxprt.stator.properties.children["Winding"].props["Number of Strands"] = 1

## Define rotor

Define rotor and pole settings.

In [11]:
rmxprt.rotor["Outer Diameter"] = "74mm"
rmxprt.rotor["Inner Diameter"] = "26mm"
rmxprt.rotor["Length"] = "65mm"
rmxprt.rotor["Stacking Factor"] = 0.95
rmxprt.rotor["Steel Type"] = "steel_1008"
rmxprt.rotor["Pole Type"] = 1

In [12]:
rmxprt.rotor.properties.children["Pole"].props["Embrace"] = 0.7
rmxprt.rotor.properties.children["Pole"].props["Offset"] = "0mm"
rmxprt.rotor.properties.children["Pole"].props["Magnet Type"] = [
    "Material:=",
    "Alnico9",
]
rmxprt.rotor.properties.children["Pole"].props["Magnet Thickness"] = "3.5mm"

## Create setup

Create a setup and define the main settings.

In [13]:
setup = rmxprt.create_setup()
setup.props["RatedVoltage"] = "220V"
setup.props["RatedOutputPower"] = "550W"
setup.props["RatedSpeed"] = "1500rpm"
setup.props["OperatingTemperature"] = "75cel"

## Analyze setup.

In [14]:
setup.analyze(cores=NUM_CORES)

PyAEDT INFO: Solving design setup MySetupAuto


PyAEDT INFO: Design setup MySetupAuto solved correctly in 0.0h 0.0m 9.0s


## Export to Maxwell

After the project is solved, you can export it to either Maxwell 2D or Maxwell 3D.

In [15]:
m2d = rmxprt.create_maxwell_design(setup_name=setup.name, maxwell_2d=True)
m2d.plot(
    show=False,
    output_file=os.path.join(temp_folder.name, "Image.jpg"),
    plot_air_objects=True,
)

PyAEDT INFO: Python version 3.10.11 (tags/v3.10.11:7d4cc5a, Apr  5 2023, 00:38:17) [MSC v.1929 64 bit (AMD64)]


PyAEDT INFO: PyAEDT version 0.12.dev0.


PyAEDT INFO: Returning found Desktop session with PID 7760!


PyAEDT INFO: No project is defined. Project ASSM exists and has been read.


PyAEDT INFO: Aedt Objects correctly read


...

PyAEDT INFO: Modeler2D class has been initialized!


PyAEDT INFO: Modeler class has been initialized! Elapsed time: 0m 0sec


PyAEDT INFO: PostProcessor class has been initialized! Elapsed time: 0m 0sec


PyAEDT INFO: Post class has been initialized! Elapsed time: 0m 0sec


C:\actions-runner\_work\pyaedt-examples\pyaedt-examples\.venv\lib\site-packages\pyvista\jupyter\notebook.py:37: UserWarning: Failed to use notebook backend: 

No module named 'trame'

Falling back to a static output.
  warnings.warn(


## Export RMxprt settings

Export all RMxprt settings to a JSON file to reuse it for another
project with the the import function.

In [16]:
config = rmxprt.export_configuration(os.path.join(temp_folder.name, "assm.json"))
rmxprt2 = ansys.aedt.core.Rmxprt(
    project="assm_test2",
    solution_type=rmxprt.solution_type,
    design="from_configuration",
)
rmxprt2.import_configuration(config)

PyAEDT INFO: C:\Users\ansys\AppData\Local\Temp\tmpyz5wuzdw.ansys\assm.json correctly created.


PyAEDT INFO: Python version 3.10.11 (tags/v3.10.11:7d4cc5a, Apr  5 2023, 00:38:17) [MSC v.1929 64 bit (AMD64)]


PyAEDT INFO: PyAEDT version 0.12.dev0.


PyAEDT INFO: Returning found Desktop session with PID 7760!


PyAEDT INFO: Project assm_test2 has been created.


PyAEDT INFO: Added design 'from_configuration' of type RMxprtSolution.


PyAEDT INFO: Aedt Objects correctly read


PyAEDT INFO: ModelerRMxprt class has been initialized! Elapsed time: 0m 0sec


True

## Save project

Save the project containing the Maxwell design.

In [17]:
m2d.save_project(file_name=project_name)

PyAEDT INFO: Project ASSM Saved correctly


True

## Release AEDT and clean up temporary directory

Release AEDT and remove both the project and temporary directory.

In [18]:
m2d.release_desktop()
time.sleep(3)
temp_folder.cleanup()

PyAEDT INFO: Desktop has been released and closed.
